# Desempenho das Escolas do Estado de São Paulo e Nível Socioeconômico
---

Foi publicado recentemento um Índice de Nível Socioeconômico (INSE) das escolas do Estado de São Paulo. 

O INSE leva em conta as seguintes variáveis:

- Grau de Escolaridade dos Pais
- Posse de bens de consumo duráveis da residência
- Renda Familiar

Onde 10 é o nível socioeconomico mais baixo e 0 o mais alto.

O Estado de São Paulo também divulga anualmente o IDESP, Índice de Desenvolvimento da Educação do Estado de São Paulo, que avalia a qualidade da escola a partir de dois critérios:

- desempenho dos alunos nos exames de proficiência do SARESP (o quanto aprenderam)
- fluco escolar (em quanto tempo aprenderam)

Essa análise explora as correlações entre o nível socioeconômico e o desempenho escolar

*Code made by [You](https://github.com/JoaoCarabetta) - João Carabetta

### Import required libraries

In [2]:
# IMPORT CONFIGs
import os
import sys
sys.path.insert(0, '../')
sys.path.insert(0, '../scripts')
from config import RAW_PATH, TREAT_PATH, OUTPUT_PATH


# DATA ANALYSIS & VIZ TOOLS
from copy import deepcopy

import pandas as pd
pd.options.display.max_columns = 999

import plotly
import plotly.graph_objs as go
import plotly.offline as offline
offline.init_notebook_mode(connected=True)

%pylab inline
pylab.rcParams['figure.figsize'] = (12, 12)


# For changes in .py
%reload_ext autoreload
%autoreload 2

import warnings
warnings.filterwarnings('ignore')

Populating the interactive namespace from numpy and matplotlib


### Import data

In [3]:
inse = pd.read_csv(RAW_PATH / 'INSE_Geral 2018_1.csv', sep=';')
inse['NIVEL SOCIOECONOMICO DOS ALUNOS'] = inse['NIVEL SOCIOECONOMICO DOS ALUNOS'].apply(lambda x: float(x.replace(',', '.')))
inse['CODESC'] = inse['CODESC'].apply(int)

In [150]:
inse['NIVEL SOCIOECONOMICO DOS ALUNOS'] = inse['NIVEL SOCIOECONOMICO DOS ALUNOS'].apply(lambda x: 10 - x)

In [151]:
inse.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5127 entries, 0 to 5126
Data columns (total 5 columns):
CODESC                             5127 non-null int64
NOMESC                             5127 non-null object
Dir                                5127 non-null object
MUN                                5127 non-null object
NIVEL SOCIOECONOMICO DOS ALUNOS    5127 non-null float64
dtypes: float64(1), int64(1), object(3)
memory usage: 200.4+ KB


In [152]:
inse.head(1)

CODESC                    NOMESC      Dir        MUN  \
0      12  AYRES DE MOURA PROFESSOR  NORTE 1  SAO PAULO   

   NIVEL SOCIOECONOMICO DOS ALUNOS  
0                             7.29

In [153]:
idesp_2018 = pd.read_csv(RAW_PATH / 'IDESP por Escola - 2018.csv', sep=';')

In [154]:
idesp_2018.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5051 entries, 0 to 5050
Data columns (total 10 columns):
ANO_LETIVO          5051 non-null int64
CODIGO_CIE          5051 non-null int64
CODIGO_INEP         5051 non-null int64
CODIGO_DIRETORIA    5051 non-null int64
NOME_DIRETORIA      5051 non-null object
NOME_ESCOLA         5051 non-null object
NOME_MUNICIPIO      5051 non-null object
ANOS_INICIAIS       1460 non-null float64
ANOS_FINAIS         3654 non-null float64
ENSINO_MEDIO        3668 non-null float64
dtypes: float64(3), int64(4), object(3)
memory usage: 394.7+ KB


In [155]:
idesp_2018.head(1)

ANO_LETIVO  CODIGO_CIE  CODIGO_INEP  CODIGO_DIRETORIA NOME_DIRETORIA  \
0        2018      909075     35909075             10208        LESTE 4   

              NOME_ESCOLA NOME_MUNICIPIO  ANOS_INICIAIS  ANOS_FINAIS  \
0  WILFREDO PINHEIRO PROF      SAO PAULO           4.97         2.92   

   ENSINO_MEDIO  
0          2.45

In [156]:
idesp_hist =  pd.read_csv(RAW_PATH / 'DBOIdespEscSerHist_2_2011_2017.csv')

In [157]:
idesp_hist.head()

CodigoCIE  CodigoINEP  CodigoDiretoria NomeDiretoria  \
0        206    35000206            10101       NORTE 1   
1       2082    35002082            10205       LESTE 5   
2       3165    35003165            10208       LESTE 4   
3        681    35000681            10102        CENTRO   
4        449    35000449            10102        CENTRO   

                                          NomeEscola NomeMunicipio  \
0  ALIPIO DE BARROS PROFESSOR                    ...     SAO PAULO   
1  BLANCA ZWICKER SIMOES PROFESSORA              ...     SAO PAULO   
2  JANDYRA VIEIRA CUNHA BARRA PROFA              ...     SAO PAULO   
3  TOLEDO BARBOSA                                ...     SAO PAULO   
4  TAUNAY VISCONDE DE                            ...     SAO PAULO   

  NivelEnsino  Ano2011  Ano2012  Ano2013  Ano2014  Ano2015  Ano2016  Ano2017  
0          AI     3.85     4.53     4.27     5.49     4.94     5.18     5.20  
1          AI     6.42     5.95     6.83     6.64     6.62     7.13     7.41  
2          AI     4.23     4.50     3.59     4.92     4.57     4.91     5.43  
3          AI     4.72     4.13     4.70     4.58     4.54     5.35     5.53  
4          AI     4.69     5.93     7.11     8.03     6.25     5.97     6.90

In [158]:
enderecos = pd.read_csv(RAW_PATH / 'escolas_enderecos_0.csv', error_bad_lines=False)

b'Skipping line 25881: expected 19 fields, saw 20\n'


In [159]:
enderecos.head()

nomedep  depadm        mun  codmun       de  CD_ESCOLA  CD_DIRETORIA  \
0  ESTADUAL - SE       1  SAO PAULO     100  NORTE 1      36444         10101   
1  ESTADUAL - SE       1  SAO PAULO     100  LESTE 5       1582         10205   
2  ESTADUAL - SE       1  SAO PAULO     100  LESTE 5       2173         10205   
3  ESTADUAL - SE       1  SAO PAULO     100  LESTE 1       3086         10207   
4  ESTADUAL - SE       1  SAO PAULO     100  LESTE 1       2884         10207   

   CD_DIRETORIA_ESTADUAL  CD_DIRETORIA_SUPVS_PROPR  \
0                  10101                     10101   
1                  10205                     10205   
2                  10205                     10205   
3                  10207                     10207   
4                  10207                     10207   

                 NM_COMPLETO_ESCOLA  CD_UNIDADE           DS_ENDERECO  \
0   GENESIO DE ALMEIDA MOURA DOUTOR       37806     DOMINGOS AREVALO    
1       DOMINGOS FAUSTINO SARMIENTO       24902          21 DE ABRIL    
2             JOAO BORGES PROFESSOR       24901              ITAPURA    
3  HELENA LOMBARDI BRAGA PROFESSORA       24918  VIRGINIA DE MIRANDA    
4               RAUL PILLA DEPUTADO       24923      RUA SAO BERTOLDO   

  COMPLEMENTO NUMERO  CD_ORIGEM_UNIDADE  CD_ORIGEM_ESCOLA  CD_ORIGEM_ENDERECO  \
0         RUA    862              37806             36444               37866   
1         RUA    970              24902              1582               24962   
2         RUA    976              24901              2173               24961   
3         RUA    138              24918              3086               24978   
4         RUA    449              24923              2884               24983   

    LATITUDE  LONGITUDE  
0 -23.447000 -46.696700  
1 -23.542232 -46.605793  
2 -23.547300 -46.566000  
3 -23.526587 -46.452888  
4 -23.494297 -46.457064

# Análises

1. Distribuição do INSE por escola
2. Correlação do INSE e IDESP por escola por nível de ensino em 2018
3. Variação da correlação no tempo
4. INSE por escola geograficamente
5. Variação IDESP geograficamente
6. Identificação das áreas mais críticas

## 1. Distribuição do INSE por escola

In [160]:
data = [go.Histogram(x=inse['NIVEL SOCIOECONOMICO DOS ALUNOS'])]

layout = go.Layout(title='Distribuição do Nível Socioeconômico dos Alunos',
                  xaxis=dict(title='INSE'),
                  yaxis=dict(title='Número de Escolas'))

figure = go.Figure(data=data, layout=layout)

offline.iplot(figure)



In [266]:
inse['NIVEL SOCIOECONOMICO DOS ALUNOS'].describe()

count    5127.000000
mean        5.423513
std         1.358798
min         0.270000
25%         4.540000
50%         5.320000
75%         6.295000
max         9.970000
Name: NIVEL SOCIOECONOMICO DOS ALUNOS, dtype: float64

## 2. Correlação do INSE e IDESP por escola por nível de ensino em 2018

In [231]:
from sklearn import  linear_model
from sklearn.metrics import mean_squared_error, r2_score

coefs = []

In [162]:
inse.head(1)

CODESC                    NOMESC      Dir        MUN  \
0      12  AYRES DE MOURA PROFESSOR  NORTE 1  SAO PAULO   

   NIVEL SOCIOECONOMICO DOS ALUNOS  
0                             7.29

In [163]:
idesp_2018.head(1)

ANO_LETIVO  CODIGO_CIE  CODIGO_INEP  CODIGO_DIRETORIA NOME_DIRETORIA  \
0        2018      909075     35909075             10208        LESTE 4   

              NOME_ESCOLA NOME_MUNICIPIO  ANOS_INICIAIS  ANOS_FINAIS  \
0  WILFREDO PINHEIRO PROF      SAO PAULO           4.97         2.92   

   ENSINO_MEDIO  
0          2.45

In [164]:
inse_idesp_2018 = inse.merge(idesp_2018, left_on='CODESC', right_on='CODIGO_CIE')
print('Número de escolas que não estão nas duas bases: ', len(inse) - len(inse_idesp_2018))

Número de escolas que não estão nas duas bases:  63


In [248]:
def plot_regression(periodo_escolar):

    regr = linear_model.LinearRegression()
    fit_data = inse_idesp_2018.dropna(subset=[periodo_escolar])
    regr.fit(fit_data['NIVEL SOCIOECONOMICO DOS ALUNOS'].values.reshape(-1, 1), 
             fit_data[periodo_escolar].values.reshape(-1, 1))

    data = []

    data.append(go.Scatter(x=fit_data['NIVEL SOCIOECONOMICO DOS ALUNOS'],
                       y=fit_data[periodo_escolar],
                       mode = 'markers'))

    data.append(go.Scatter(x=fit_data['NIVEL SOCIOECONOMICO DOS ALUNOS'], 
                    y=regr.predict(fit_data['NIVEL SOCIOECONOMICO DOS ALUNOS'].values.reshape(-1, 1)).reshape(1, -1).tolist()[0],
                    mode='lines',
                    line=dict(color='black', width=3),

                    ))

    layout = go.Layout(title=f'INSE x IDESP para {periodo_escolar}',
                      xaxis=dict(title='INSE'),
                      yaxis=go.YAxis(title='IDESP', range=[0, 10]))

    figure = go.Figure(data=data, layout=layout)

    offline.iplot(figure)

    # The coefficients
    print('Linear Model:')
    print('y = Ax + b')
    print(f'y = {round(regr.coef_[0][0], 2)}x + {round(regr.intercept_[0], 2)}')
    # The mean squared error
     # Explained variance score: 1 is perfect prediction
    print('R^2: %.2f' % r2_score(fit_data[periodo_escolar].values.reshape(-1, 1),
                                 regr.predict(fit_data['NIVEL SOCIOECONOMICO DOS ALUNOS'].values.reshape(-1, 1))))
    
    return {'coef': regr.coef_[0][0], 'categoria_escolar': periodo_escolar, 'ano': 2018}

In [252]:
coefs.append(plot_regression('ANOS_INICIAIS'))

Linear Model:
y = Ax + b
y = 0.24x + 4.36
R^2: 0.09


In [253]:
coefs.append(plot_regression('ANOS_FINAIS'))

Linear Model:
y = Ax + b
y = 0.17x + 2.48
R^2: 0.08


In [254]:
coefs.append(plot_regression('ENSINO_MEDIO'))

Linear Model:
y = Ax + b
y = 0.15x + 1.77
R^2: 0.07


In [169]:
df_coefs = pd.DataFrame(coefs)

In [170]:
data = [go.Bar(x=df_coefs['categoria_escolar'],
      y=df_coefs['coef'])]

layout = go.Layout(title=f'Comparação dos Coeficientes Angulares por Categoria Escolar',
                  xaxis=dict(title='INSE'),
                  yaxis=go.YAxis(title='IDESP'))

figure = go.Figure(data=data, layout=layout)

offline.iplot(figure)

## 3. Variação da correlação no tempo

### Une série histórica com 2018

In [171]:
idesp_melted = idesp_hist.melt(id_vars=['CodigoCIE', 'NivelEnsino'], value_vars=['Ano2011', 'Ano2012',
   'Ano2013', 'Ano2014', 'Ano2015', 'Ano2016', 'Ano2017'],)
idesp_melted['NivelEnsino'] = idesp_melted['NivelEnsino'].replace({'AI': 'ANOS_INICIAIS', 'AF': 'ANOS_FINAIS', 'EM':'ENSINO_MEDIO'})
idesp_temp = idesp_2018.melt(id_vars='CODIGO_CIE', value_vars=['ANOS_INICIAIS', 'ANOS_FINAIS', 'ENSINO_MEDIO'], 
                            var_name='NivelEnsino')
idesp_temp['variable'] = 'Ano2018'
idesp_temp = idesp_temp.rename(columns={'CODIGO_CIE': 'CodigoCIE'})
idesp_melted = pd.concat([idesp_melted, idesp_temp]).rename(columns={'value': 'IDESP', 'variable': 'Ano'})
idesp_melted['Ano'] = idesp_melted['Ano'].apply(lambda x: int(x.replace('Ano', '')))

In [172]:
inse.head()

CODESC                                  NOMESC      Dir        MUN  \
0      12                AYRES DE MOURA PROFESSOR  NORTE 1  SAO PAULO   
1      24               GAVIAO PEIXOTO BRIGADEIRO  NORTE 1  SAO PAULO   
2      36                            JOAO SOLIMEO  NORTE 1  SAO PAULO   
3      48       WALFREDO ARANTES CALDAS PROFESSOR  NORTE 1  SAO PAULO   
4      59  SEBASTIAO DE OLIVEIRA GUSMAO PROFESSOR  NORTE 1  SAO PAULO   

   NIVEL SOCIOECONOMICO DOS ALUNOS  
0                             7.29  
1                             6.07  
2                             5.98  
3                             5.73  
4                             5.96

In [173]:
inse_idesp = idesp_melted.merge(inse, right_on='CODESC', left_on='CodigoCIE')

In [174]:

def get_regression_coef(ano, nivel_ensino):

    regr = linear_model.LinearRegression()

    df = inse_idesp.query(f'Ano == {ano}').query(f"NivelEnsino == '{nivel_ensino}'")
    
    df = df.dropna(subset=['IDESP'])
    
    regr.fit(df['NIVEL SOCIOECONOMICO DOS ALUNOS'].values.reshape(-1, 1), 
         df['IDESP'].values.reshape(-1, 1))
    
    return {'coef': regr.coef_[0][0], 'nivel_ensino': nivel_ensino, 'ano': ano}

In [175]:
coefs = []
for ano in inse_idesp['Ano'].unique():
    for nivel_ensino in inse_idesp['NivelEnsino'].unique():
        coefs.append(get_regression_coef(ano, nivel_ensino))

In [176]:
df_coefs = pd.DataFrame(coefs)
df_coefs = df_coefs.sort_values(by='ano')

In [177]:
df_coefs.query(f"nivel_ensino == '{nivel_ensino}'")

ano      coef  nivel_ensino
2   2011  0.123468  ENSINO_MEDIO
5   2012  0.121588  ENSINO_MEDIO
8   2013  0.129164  ENSINO_MEDIO
11  2014  0.131467  ENSINO_MEDIO
14  2015  0.107574  ENSINO_MEDIO
17  2016  0.130394  ENSINO_MEDIO
20  2017  0.138752  ENSINO_MEDIO
23  2018  0.145040  ENSINO_MEDIO

In [206]:
data = []

for nivel_ensino in inse_idesp['NivelEnsino'].unique():
    
    data.append(go.Scatter(x=df_coefs.query(f"nivel_ensino == '{nivel_ensino}'")['ano'],
                  y=df_coefs.query(f"nivel_ensino == '{nivel_ensino}'")['coef'],
                          name=nivel_ensino)),
               

layout = go.Layout(title='Variação da Desigualdade por Nível de Ensino',
                  xaxis=dict(title='Anos'),
                  yaxis=go.YAxis(title='Desigualdade\n(Coeficiente Angular)'),
                    autosize=False,
                    width=600,
                    height=600,
                   legend=go.Legend(xanchor='rigth'))

figure = go.Figure(data=data, layout=layout)

offline.iplot(figure)

## 4. Variação IDESP x INSE

In [179]:
variacoes = []
for nivel_ensino in inse_idesp['NivelEnsino'].unique():
    
    variacao = (((inse_idesp.query(f'Ano == 2018').query(f"NivelEnsino == '{nivel_ensino}'").set_index('CodigoCIE')['IDESP'] - 
inse_idesp.query(f'Ano == 2011').query(f"NivelEnsino == '{nivel_ensino}'").set_index('CodigoCIE')['IDESP']) / 
inse_idesp.query(f'Ano == 2011').query(f"NivelEnsino == '{nivel_ensino}'").set_index('CodigoCIE')['IDESP']) * 100).to_frame()
    
    variacao['nivel_ensino'] = nivel_ensino
    
    variacoes.append(variacao)
variacoes = pd.concat(variacoes)    

In [180]:
nivel_ensino='ENSINO_MEDIO'

In [181]:
variacoes = variacoes.merge(inse[['CODESC', 'NIVEL SOCIOECONOMICO DOS ALUNOS']], left_index=True, right_on='CODESC')

In [182]:
variacoes.head()

IDESP   nivel_ensino  CODESC  NIVEL SOCIOECONOMICO DOS ALUNOS
0        NaN  ANOS_INICIAIS      12                             7.29
0  74.793388    ANOS_FINAIS      12                             7.29
0        NaN   ENSINO_MEDIO      12                             7.29
1        NaN  ANOS_INICIAIS      24                             6.07
1   0.414938    ANOS_FINAIS      24                             6.07

In [263]:
data = [go.Histogram(x = variacoes[(variacoes['nivel_ensino'] == 'ANOS_INICIAIS') &
          (variacoes['IDESP'] < 200)
         ].drop_duplicates(subset=['CODESC'])['IDESP'])]
layout = go.Layout(title=f'Variação do IDESP de 2011 a 2018 para Anos Iniciais',
                  xaxis=dict(title='Variação em %'),
                  yaxis=go.YAxis(title='Número de Escolas'),
                    autosize=False,
                    width=600,
                    height=600,)

figure = go.Figure(data=data, layout=layout)

offline.iplot(figure)

variacoes[(variacoes['nivel_ensino'] == 'ANOS_INICIAIS') ].drop_duplicates(subset=['CODESC']).describe()

IDESP         CODESC  NIVEL SOCIOECONOMICO DOS ALUNOS
count  1411.000000    5090.000000                       5090.00000
mean     34.140473  280728.224754                          5.42522
std      32.874417  392555.585467                          1.36082
min     -37.277354      12.000000                          0.27000
25%      13.948422   16062.250000                          4.54000
50%      29.455446   35683.000000                          5.32000
75%      49.409081  901483.000000                          6.30000
max     381.818182  926103.000000                          9.97000

In [264]:
data = [go.Histogram(x = variacoes[(variacoes['nivel_ensino'] == 'ANOS_FINAIS') &
          (variacoes['IDESP'] < 200)].drop_duplicates(subset=['CODESC'])['IDESP'])]
layout = go.Layout(title=f'Variação do IDESP de 2011 a 2018 para Anos Finais',
                  xaxis=dict(title='Variação em %'),
                  yaxis=go.YAxis(title='Número de Escolas'))

figure = go.Figure(data=data, layout=layout)

offline.iplot(figure)

variacoes[(variacoes['nivel_ensino'] == 'ANOS_FINAIS') ].drop_duplicates(subset=['CODESC']).describe()

IDESP         CODESC  NIVEL SOCIOECONOMICO DOS ALUNOS
count  3466.000000    5072.000000                      5072.000000
mean     32.732255  280372.098778                         5.429405
std      32.276673  392300.378291                         1.360822
min     -69.449715      12.000000                         0.270000
25%      11.819392   16016.750000                         4.550000
50%      28.571429   35659.500000                         5.330000
75%      49.387755  901493.500000                         6.300000
max     353.164557  926103.000000                         9.970000

In [265]:
data = [go.Histogram(x = variacoes[(variacoes['nivel_ensino'] == 'ENSINO_MEDIO') &
          (variacoes['IDESP'] < 200)
         ].drop_duplicates(subset=['CODESC'])['IDESP'])]
layout = go.Layout(title=f'Variação do IDESP de 2011 a 2018 para Ensino Médio',
                  xaxis=dict(title='Variação em %'),
                  yaxis=go.YAxis(title='Número de Escolas'))

figure = go.Figure(data=data, layout=layout)

offline.iplot(figure, image_width=800, image_height=800)

variacoes[(variacoes['nivel_ensino'] == 'ENSINO_MEDIO') ].drop_duplicates(subset=['CODESC']).describe()

IDESP         CODESC  NIVEL SOCIOECONOMICO DOS ALUNOS
count  3428.000000    5067.000000                      5067.000000
mean     50.640333  279811.308072                         5.430892
std      49.965085  392065.043700                         1.359558
min     -77.595628      12.000000                         0.270000
25%      19.413853   15994.500000                         4.550000
50%      42.206448   35634.000000                         5.330000
75%      71.852245  901401.000000                         6.300000
max     812.121212  926103.000000                         9.970000

In [228]:
def plot_regression_a(nivel_ensino):

    regr = linear_model.LinearRegression()
    df = variacoes[variacoes['nivel_ensino'] == nivel_ensino]
    fit_data = df.dropna(subset=['IDESP']).drop_duplicates(subset=['CODESC'])
    regr.fit(fit_data['NIVEL SOCIOECONOMICO DOS ALUNOS'].values.reshape(-1, 1), 
             fit_data['IDESP'].values.reshape(-1, 1))

    data = []

    data.append(go.Scatter(x=df['NIVEL SOCIOECONOMICO DOS ALUNOS'],
                       y=df['IDESP'],
                       mode = 'markers'))

    data.append(go.Scatter(x=df['NIVEL SOCIOECONOMICO DOS ALUNOS'], 
                    y=regr.predict(df['NIVEL SOCIOECONOMICO DOS ALUNOS'].values.reshape(-1, 1)).reshape(1, -1).tolist()[0],
                    mode='lines',
                    line=dict(color='black', width=3),

                    ))

    layout = go.Layout(title=f'INSE x IDESP para {nivel_ensino}',
                      xaxis=dict(title='INSE'),
                      yaxis=go.YAxis(title='IDESP'))

    figure = go.Figure(data=data, layout=layout)

    offline.iplot(figure)

    # The coefficients
    print('Linear Model:')
    print('y = Ax + b')
    print(f'y = {round(regr.coef_[0][0], 2)}x + {round(regr.intercept_[0], 2)}')
    return regr

In [229]:
regr = plot_regression_a('ANOS_INICIAIS')

Linear Model:
y = Ax + b
y = -3.5x + 52.26


In [255]:
plot_regression_a('ANOS_FINAIS')

Linear Model:
y = Ax + b
y = -2.11x + 44.14


LinearRegression(copy_X=True, fit_intercept=True, n_jobs=None,
         normalize=False)

In [256]:
plot_regression_a('ENSINO_MEDIO')

Linear Model:
y = Ax + b
y = -2.3x + 63.28


LinearRegression(copy_X=True, fit_intercept=True, n_jobs=None,
         normalize=False)

## 5. INSE por escola geograficamente

In [187]:
enderecos_inse = enderecos.merge(inse, left_on='CD_ESCOLA', right_on='CODESC')
enderecos_inse = enderecos_inse[['CD_ESCOLA', 'MUN', 'NM_COMPLETO_ESCOLA', 'DS_ENDERECO', 'LATITUDE', 'LONGITUDE', 'NIVEL SOCIOECONOMICO DOS ALUNOS']]



In [188]:
enderecos_inse = enderecos_inse.merge(variacoes.drop_duplicates().pivot(index='CODESC', columns='nivel_ensino', values='IDESP').reset_index(),
                     left_on='CD_ESCOLA', right_on='CODESC')

In [189]:
enderecos_inse = enderecos_inse.rename(columns={x: x + '_var' for x in ['ANOS_FINAIS', 'ANOS_INICIAIS', 'ENSINO_MEDIO']})

In [190]:
idesp_2018.columns

Index(['ANO_LETIVO', 'CODIGO_CIE', 'CODIGO_INEP', 'CODIGO_DIRETORIA',
       'NOME_DIRETORIA', 'NOME_ESCOLA', 'NOME_MUNICIPIO', 'ANOS_INICIAIS',
       'ANOS_FINAIS', 'ENSINO_MEDIO'],
      dtype='object')

In [191]:
enderecos_inse = enderecos_inse.merge(idesp_2018[['CODIGO_CIE','ANOS_INICIAIS', 'ANOS_FINAIS', 'ENSINO_MEDIO' ]], right_on='CODIGO_CIE', left_on='CD_ESCOLA')

In [192]:
enderecos_inse.head()

CD_ESCOLA        MUN                NM_COMPLETO_ESCOLA  \
0      36444  SAO PAULO   GENESIO DE ALMEIDA MOURA DOUTOR   
1       1582  SAO PAULO       DOMINGOS FAUSTINO SARMIENTO   
2       2173  SAO PAULO             JOAO BORGES PROFESSOR   
3       3086  SAO PAULO  HELENA LOMBARDI BRAGA PROFESSORA   
4       2884  SAO PAULO               RAUL PILLA DEPUTADO   

            DS_ENDERECO   LATITUDE  LONGITUDE  \
0     DOMINGOS AREVALO  -23.447000 -46.696700   
1          21 DE ABRIL  -23.542232 -46.605793   
2              ITAPURA  -23.547300 -46.566000   
3  VIRGINIA DE MIRANDA  -23.526587 -46.452888   
4      RUA SAO BERTOLDO -23.494297 -46.457064   

   NIVEL SOCIOECONOMICO DOS ALUNOS  CODESC  ANOS_FINAIS_var  \
0                             4.61   36444         8.092486   
1                             4.56    1582              NaN   
2                             9.72    2173        17.444717   
3                             6.30    3086        54.945055   
4                             5.27    2884       106.074766   

   ANOS_INICIAIS_var  ENSINO_MEDIO_var  CODIGO_CIE  ANOS_INICIAIS  \
0           8.366534        125.396825       36444           2.72   
1          38.483965               NaN        1582           4.75   
2                NaN         15.217391        2173            NaN   
3                NaN         41.614907        3086            NaN   
4                NaN               NaN        2884            NaN   

   ANOS_FINAIS  ENSINO_MEDIO  
0         1.87          1.42  
1          NaN           NaN  
2         4.78          3.71  
3         2.82          2.28  
4         4.41           NaN

In [193]:
enderecos_inse.to_csv(OUTPUT_PATH / 'enderecos_indices.csv')

In [194]:
enderecos_inse

CD_ESCOLA                    MUN  \
0         36444              SAO PAULO   
1          1582              SAO PAULO   
2          2173              SAO PAULO   
3          3086              SAO PAULO   
4          2884              SAO PAULO   
5         35610              SAO PAULO   
6          4388              SAO PAULO   
7          4424              SAO PAULO   
8          1739              SAO PAULO   
9          4947              SAO PAULO   
10       906530              SAO PAULO   
11       906585              SAO PAULO   
12        46361              SAO PAULO   
13       901805               CAIEIRAS   
14        44957       FRANCISCO MORATO   
15       924167       FRANCISCO MORATO   
16         5885              GUARULHOS   
17         6026              GUARULHOS   
18        41919              GUARULHOS   
19       285785              GUARULHOS   
20       908459              GUARULHOS   
21       916924        MOGI DAS CRUZES   
22        35531  FERRAZ DE VASCONCELOS   
23       908927  FERRAZ DE VASCONCELOS   
24        46197                 SUZANO   
25         7298                    POA   
26         7959         RIBEIRAO PIRES   
27         8357            SANTO ANDRE   
28       925123              GUARULHOS   
29        39342              SAO PAULO   
...         ...                    ...   
5121     909610            HORTOLANDIA   
5122      18545               CAMPINAS   
5123       7024                 SUZANO   
5124       7109        ITAQUAQUECETUBA   
5125     916584        ITAQUAQUECETUBA   
5126     917102        ITAQUAQUECETUBA   
5127       7341                DIADEMA   
5128      39329                DIADEMA   
5129     910235                DIADEMA   
5130       7778                   MAUA   
5131       7845                   MAUA   
5132       8278            SANTO ANDRE   
5133       8345            SANTO ANDRE   
5134       8813  SAO BERNARDO DO CAMPO   
5135      39548  SAO BERNARDO DO CAMPO   
5136       9817            CARAPICUIBA   
5137       9885            CARAPICUIBA   
5138      40733   ITAPECERICA DA SERRA   
5139     918659   ITAPECERICA DA SERRA   
5140     910485                BARUERI   
5141      40770                 OSASCO   
5142     924039                 OSASCO   
5143      48422         EMBU DAS ARTES   
5144     921749               BERTIOGA   
5145      11721                 SANTOS   
5146      11757                 SANTOS   
5147      37576            SAO VICENTE   
5148      12725                  POTIM   
5149      13626    SAO JOSE DOS CAMPOS   
5150      13912    SAO JOSE DOS CAMPOS   

                                NM_COMPLETO_ESCOLA  \
0                  GENESIO DE ALMEIDA MOURA DOUTOR   
1                      DOMINGOS FAUSTINO SARMIENTO   
2                            JOAO BORGES PROFESSOR   
3                 HELENA LOMBARDI BRAGA PROFESSORA   
4                              RAUL PILLA DEPUTADO   
5     RENATA GRAZIANO DE OLIVEIRA PRADO PROFESSORA   
6                SEMINARIO NOSSA SENHORA DA GLORIA   
7                          FRANCISCO DE ASSIS REYS   
8                          ANDRE DREYFUS PROFESSOR   
9             NEYDE APPARECIDA SOLLITTO PROFESSORA   
10            ETELVINA DE GOES MARCUCCI PROFESSORA   
11                       JAYR DE ANDRADE PROFESSOR   
12                          ESTHER GARCIA PROFA EE   
13                          MARIO TOLEDO DE MORAES   
14                                VINCENZO LOBASSI   
15                         PARQUE CENTO E VINTE II   
16                                          ROTARY   
17                          ANTONIO DE RE VEREADOR   
18                          SEBASTIAO WALTER FUSCO   
19                       REPUBLICA DA VENEZUELA II   
20                 WANDA MASCAGNI DE SA PROFESSORA   
21                     EURYCLIDES DE JESUS ZERBINI   
22               PAULO AMERICO PAGANUCCI PROFESSOR   
23                       OLZANETTI GOMES PROFESSOR   
24                                  CHOJIRO SEGAWA 